In [1]:
!pip install translators

import pandas as pd
# current version have logs, which is not very comfortable
import translators as ts
from multiprocessing import Pool
from tqdm import *
import random

import sklearn
from sklearn.model_selection import StratifiedKFold
from sklearn.model_selection import train_test_split

     |████████████████████████████████| 56 kB 501 kB/s 
  Created wheel for PyExecJS: filename=PyExecJS-1.5.1-py3-none-any.whl size=14588 sha256=37bfb02ecc35012d2ec3812917ac5b2120e6dde5d585ef0405203d343e8bed6a
  Stored in directory: /root/.cache/pip/wheels/9a/ee/03/da5c0b4a8c13362beeb844eb913bbe58a89bde1de2b9157007
Successfully built PyExecJS
You should consider upgrading via the '/opt/conda/bin/python3.7 -m pip install --upgrade pip' command.


Using Belgium server backend.


In [2]:
#set random seed
def set_seed(seed: int = 123):
    random.seed(seed)
    #np.random.seed(seed)
    #os.environ["PYTHONHASHSEED"] = str(seed)
    #torch.manual_seed(seed)
    #torch.cuda.manual_seed(seed)  # type: ignore
    #torch.backends.cudnn.deterministic = True  # type: ignore
    #torch.backends.cudnn.benchmark = True  # type: ignore
    
set_seed(123)

In [3]:
def translator_constructor(api):
    if api == 'google':
        return ts.google
    elif api == 'bing':
        return ts.bing
    elif api == 'baidu':
        return ts.baidu
    elif api == 'sogou':
        return ts.sogou
    elif api == 'youdao':
        return ts.youdao
    elif api == 'tencent':
        return ts.tencent
    elif api == 'alibaba':
        return ts.alibaba
    else:
        raise NotImplementedError(f'{api} translator is not realised!')

In [4]:
def imap_unordered_bar(func, args, n_processes: int = 48):
    p = Pool(n_processes, maxtasksperchild=100)
    res_list = []
    with tqdm(total=len(args)) as pbar:
        for i, res in enumerate(p.imap_unordered(func, args)):
            pbar.update()
            res_list.append(res)
    pbar.close()
    p.close()
    p.join()
    return res_list

In [5]:
def translate(x):
    if len(x) >= 3:
        try:
            res = [x[0], translator_constructor(API)(x[1], 'en', LANG), x[2]]
            return [res[0], translator_constructor(API)(res[1], LANG, "en"), x[2]]
        except:
            print('hello')
            return [x[0], None, x[2]]
    else:
        try:
            res = [x[0], translator_constructor(API)(x[1], 'en', LANG)]
            return [res[0], translator_constructor(API)(res[1], LANG, "en")]
        except:
            return [x[0], None]
    

In [6]:
def translate_ver2(x):
    if x[2] == 1:
        is_trans = True if random.random() <= 0.8 else False
    elif x[2] == 2:
        is_trans = True if random.random() <= 0.9 else False
    elif x[2] == 3:
        is_trans = True if random.random() <= 0.7 else False
    elif x[2] == 4:
        is_trans = True if random.random() <= 0.8 else False

    if is_trans:
        try:
            res = [x[0], translator_constructor(API)(x[1], 'en', LANG), x[2]]
            return [res[0], translator_constructor(API)(res[1], LANG, "en"), res[2]]
        except:
            return [x[0], None, x[2]]
    else:
        return [x[0], None, x[2]]

In [7]:
def get_new_df(df, ver2=False):
    if not ver2:
        if df.shape[1] >= 3:
            tqdm.pandas('Translation progress')
            df[['id', 'description', 'jobflag']] = imap_unordered_bar(translate, df[['id', 'description', 'jobflag']].values)
        else:
            tqdm.pandas('Translation progress')
            df[['id', 'description']] = imap_unordered_bar(translate, df[['id', 'description']].values)

        df = df.dropna()
        return df
    
    else:
        if df.shape[1] >= 3:
            tqdm.pandas('Translation progress')
            df[['id', 'description', 'jobflag']] = imap_unordered_bar(translate_ver2, df[['id', 'description', 'jobflag']].values)
        else:
            tqdm.pandas('Translation progress')
            df[['id', 'description']] = imap_unordered_bar(translate_ver2, df[['id', 'description']].values)

        df = df.dropna()
        return df

In [8]:
def main_for_holdout():
    SPLIT_RATE = 0.8
    n_train = int(len(file)*SPLIT_RATE)
    n_val = len(file) - n_train
    train, val_dataset = train_test_split(file, train_size=n_train, test_size=n_val, random_state=123)
    val_dataset.to_csv('stcup2020-val.csv', index=False)
    
    save_PATH = f'stcup2020-train-{API}-{LANG}-holdout.csv'
    df = get_new_df(train, ver2)
    df.to_csv(save_PATH, index=False)

In [9]:
def main_for_pseudo_kfold():
    skf = StratifiedKFold(nfold, shuffle=True, random_state=124)
    FOLD = 1
    for tr_idx, val_idx in skf.split(file, file.jobflag):
        val = file.iloc[val_idx]
        val.to_csv(f'stcup2020-val-pseudo-{API}-fold{FOLD}.csv')
        save_PATH = f'stcup2020-train-pseudo-{API}-{LANG}-fold{FOLD}.csv'
        df = get_new_df(file.iloc[tr_idx], ver2)
        df.to_csv(save_PATH, index=False)
        FOLD += 1

In [10]:
def main_for_kfold():
    skf = StratifiedKFold(nfold, random_state=123)
    FOLD = 1
    for tr_idx, val_idx in skf.split(file, file.jobflag):
        val = file.iloc[val_idx]
        val.to_csv(f'stcup2020-val-new-{API}-fold{FOLD}.csv')
        save_PATH = f'stcup2020-train-new-{API}-{LANG}-fold{FOLD}.csv'
        df = get_new_df(file.iloc[tr_idx], ver2)
        df.to_csv(save_PATH, index=False)
        FOLD += 1

In [11]:
def main_for_all():
    save_PATH = f'stcup2020-{filename}-{API}-{LANG}-all.csv'
    df = get_new_df(file, ver2)
    df.to_csv(save_PATH, index=False)

In [12]:
##### config #####
languages = ['bg', 'de', 'ar', 'hi', 'sw', 'vi', 'es', 'el']
train = pd.read_csv('../input/stcup2020-new-train-dataset/new_train.csv')
test = pd.read_csv('../input/signate-stcup2020-new/test.csv')
API = 'google'
nfold = 3
pseudo = pd.read_csv('../input/987pseudo/3_BRE_XA98.7_pseudo.csv')
#pseudo = pd.read_csv('../input/98-5-pseudo/2_BRE_XA98.5_pseudo (1).csv')

##### %%%%% #####

if __name__ == '__main__':
    for LANG in languages:
        
        filename = "test"
        file = test
        ver2 = False
        #main_for_all()
        
        filename = "train"
        file = train
        ver2 = False
        #main_for_all()
        
        ver2 = False
        #main_for_kfold()
        
        file = pd.concat([train, pseudo], join='inner').reset_index(drop=True)
        main_for_pseudo_kfold()
        #main_for_holdout()

/opt/conda/lib/python3.7/site-packages/tqdm/std.py:666: FutureWarning: The Panel class is removed from pandas. Accessing it from the top-level namespace will also be removed in the next version
  from pandas import Panel
  0%|          | 0/2228 [00:00<?, ?it/s]

[10:03:32] UseTimeSeconds(fn: google_api): 0.83
[10:03:32] UseTimeSeconds(fn: google_api): 1.0
[10:03:32] UseTimeSeconds(fn: google_api): 1.15
[10:03:32] UseTimeSeconds(fn: google_api): 1.09
[10:03:32] UseTimeSeconds(fn: google_api): 1.1
[10:03:32] UseTimeSeconds(fn: google_api): 1.11
[10:03:32] UseTimeSeconds(fn: google_api): 1.17
[10:03:32] UseTimeSeconds(fn: google_api): 1.13
[10:03:32] UseTimeSeconds(fn: google_api): 1.15
[10:03:32] UseTimeSeconds(fn: google_api): 1.2
[10:03:32] UseTimeSeconds(fn: google_api): 1.19
[10:03:32] UseTimeSeconds(fn: google_api): 1.2
[10:03:32] UseTimeSeconds(fn: google_api): 1.23
[10:03:32] UseTimeSeconds(fn: google_api): 1.21
[10:03:32] UseTimeSeconds(fn: google_api): 1.26
[10:03:32] UseTimeSeconds(fn: google_api): 1.25
[10:03:32] UseTimeSeconds(fn: google_api): 1.26
[10:03:32] UseTimeSeconds(fn: google_api): 1.31
[10:03:32] UseTimeSeconds(fn: google_api): 1.27
[10:03:32] UseTimeSeconds(fn: google_api): 1.37
[10:03:32] UseTimeSeconds(fn: google_api): 1

  0%|          | 1/2228 [00:01<1:01:45,  1.66s/it]

[10:03:33] UseTimeSeconds(fn: google_api): 1.64
[10:03:33] UseTimeSeconds(fn: google_api): 0.78
[10:03:33] UseTimeSeconds(fn: google_api): 0.69
[10:03:33] UseTimeSeconds(fn: google_api): 1.64
[10:03:33] UseTimeSeconds(fn: google_api): 1.64
[10:03:33] UseTimeSeconds(fn: google_api): 0.52
[10:03:33] UseTimeSeconds(fn: google_api): 1.66
[10:03:33] UseTimeSeconds(fn: google_api): 1.66
[10:03:33] UseTimeSeconds(fn: google_api): 0.56
[10:03:33] UseTimeSeconds(fn: google_api): 0.52


  0%|          | 6/2228 [00:01<43:25,  1.17s/it]  

...

[10:25:20] UseTimeSeconds(fn: google_api): 0.72
[10:25:20] UseTimeSeconds(fn: google_api): 0.35
[10:25:20] UseTimeSeconds(fn: google_api): 0.43
[10:25:20] UseTimeSeconds(fn: google_api): 0.51
[10:25:20] UseTimeSeconds(fn: google_api): 0.85
[10:25:20] UseTimeSeconds(fn: google_api): 0.59
[10:25:20] UseTimeSeconds(fn: google_api): 0.56
[10:25:20] UseTimeSeconds(fn: google_api): 0.45
[10:25:20] UseTimeSeconds(fn: google_api): 0.66
[10:25:20] UseTimeSeconds(fn: google_api): 0.78


 30%|██▉       | 667/2228 [00:19<00:48, 32.52it/s]

[10:25:20] UseTimeSeconds(fn: google_api): 0.66
[10:25:20] UseTimeSeconds(fn: google_api): 0.46
[10:25:20] UseTimeSeconds(fn: google_api): 0.83
[10:25:20] UseTimeSeconds(fn: google_api): 0.58
[10:25:20] UseTimeSeconds(fn: google_api): 0.47


 30%|███       | 671/2228 [00:19<00:46, 33.22it/s]

[10:25:20] UseTimeSeconds(fn: google_api): 0.63
[10:25:20] UseTimeSeconds(fn: google_api): 0.69
[10:25:20] UseTimeSeconds(fn: google_api): 0.79
[10:25:20] UseTimeSeconds(fn: google_api): 0.78
[10:25:20] UseTimeSeconds(fn: google_api): 0.72
[10:25:20] UseTimeSeconds(fn: google_api): 0.42
[10:25:20] UseTimeSeconds(fn: google_api): 0.57
[10:25:20] UseTimeSeconds(fn: google_api): 0.77
[10:25:20] UseTimeSeconds(fn: google_api): 0.87
[10:25:20] UseTimeSeconds(fn: google_api): 0.84
